In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import rcParams
import seaborn as sns
import datetime
import pickle
import os
from IPython.display import display
pd.options.display.max_columns = None
%matplotlib inline

In [3]:
os.chdir("..")
total_df = pd.read_pickle('total_df.pckl.gz', compression = 'gzip')
init = pd.read_csv('Initiation.csv', low_memory=False)
dispo = pd.read_csv('Dispositions.csv', low_memory=False)
sent = pd.read_csv('Sentencing.csv', low_memory=False)

## Looking at datatype, missing values, and value distribution of input features. 

In [26]:
set(dispo.dtypes)
set(init.dtypes)
set(sent.dtypes)

{dtype('bool'), dtype('int64'), dtype('float64'), dtype('O')}

In [33]:
id_cols = ['CASE_ID', 'CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID']

In [38]:
def make_input_df(df):
    ''' 
    function to make a informational table with the data type, number of missing values, and
    value distribution information for each column of a dataframe
    '''
    input_df = pd.DataFrame([], index = df.columns, columns = ['Datatype', 
                                                               'Number of Missing Values',
                                                               'Value Information'])
    for col in df.columns:
        dtype = df[col].dtype
        input_df.loc[col]['Number of Missing Values'] = df[col].isnull().sum()  
        input_df.loc[col]['Datatype'] = dtype
        if dtype == object:
            top2 = df[col].value_counts(normalize=True)[0:2]
            distr = 'Top category: ' + str(top2.index[0]) + ' (' + format(top2[0], '.2f') + \
            '%) ' + 'Second category: ' + str(top2.index[1]) + ' (' + format(top2[1], '.2f') + '%)'
        elif dtype == 'int64' or dtype == 'float64':
            if col in id_cols:
                top2 = df[col].value_counts(normalize=True)[0:2]
                cat1 = 'Top id: ' + str(top2.index[0])
                val1 = format(top2.iloc[0], '.2f') + '%'
                cat2 = 'Second top id: ' + str(top2.index[1])
                val2 = format(top2.iloc[1], '.2f') + '%'
                distr = cat1 + ' (' + val1 + ') '+ cat2 + ' (' + val2 + ') '
            else: 
                minimum = 'Min: ' + str(min(df[col]))
                maximum = ' Max: ' + str(max(df[col]))
                mean =  ' Mean: ' + format(np.mean(df[col]), '.2f')
                median = ' Median: ' + str(np.median(df[col]))
                distr = minimum + maximum + mean + median
        elif dtype == 'bool': 
            trues = df[col].value_counts()[1]/len(df[col])
            falses = df[col].value_counts()[0]/len(df[col])
            distr = 'True: ' + format(trues, '.2f') + '%' + ' False: ' \
            + format(falses, '.2f') + '%'
        input_df.loc[col]['Value Information'] = distr
    return input_df

In [40]:
sent_input_df = make_input_df(sent)
#sent_input_df.to_csv('sent_input_df')
sent_input_df

Datatype Number of Missing Values  \
CASE_ID                              int64                        0   
CASE_PARTICIPANT_ID                  int64                        0   
OFFENSE_CATEGORY                    object                        0   
PRIMARY_CHARGE                        bool                        0   
CHARGE_ID                            int64                        0   
CHARGE_VERSION_ID                    int64                        0   
DISPOSITION_CHARGED_OFFENSE_TITLE   object                        0   
DISPOSITION_CHARGED_CHAPTER         object                        0   
DISPOSITION_CHARGED_ACT             object                     5363   
DISPOSITION_CHARGED_SECTION         object                     5363   
DISPOSITION_CHARGED_CLASS           object                       19   
DISPOSITION_CHARGED_AOIC            object                       24   
DISPOSITION_DATE                    object                        0   
CHARGE_DISPOSITION                  object                        0   
CHARGE_DISPOSITION_REASON           object                   235311   
SENTENCE_PHASE                      object                        0   
SENTENCE_DATE                       object                        0   
SENTENCE_JUDGE                      object                      742   
SENTENCE_TYPE                       object                        0   
CURRENT_SENTENCE                      bool                        0   
COMMITMENT_TYPE                     object                     1579   
COMMITMENT_TERM                     object                     1608   
COMMITMENT_UNIT                     object                     1608   
COURT_NAME                          object                     1383   
COURT_FACILITY                      object                     1866   
LENGTH_OF_CASE_in_Days             float64                    18774   
AGE_AT_INCIDENT                    float64                     3053   
GENDER                              object                      790   
RACE                                object                     1234   
INCIDENT_BEGIN_DATE                 object                     2298   
INCIDENT_END_DATE                   object                   214264   
ARREST_DATE                         object                     4880   
LAW_ENFORCEMENT_AGENCY              object                      267   
UNIT                                object                   160509   
INCIDENT_CITY                       object                    18594   
RECEIVED_DATE                       object                        0   
ARRAIGNMENT_DATE                    object                    18774   
UPDATED_OFFENSE_CATEGORY            object                        0   
CHARGE_COUNT                         int64                        0   

                                                                   Value Information  
CASE_ID                            Top id: 54249183118 (0.00%) Second top id: 628...  
CASE_PARTICIPANT_ID                Top id: 223203818277 (0.00%) Second top id: 25...  
OFFENSE_CATEGORY                   Top category: Narcotics (0.27%) Second categor...  
PRIMARY_CHARGE                                              True: 0.71% False: 0.29%  
CHARGE_ID                          Top id: 2183685557319 (0.00%) Second top id: 2...  
CHARGE_VERSION_ID                  Top id: 496433120166 (0.00%) Second top id: 49...  
DISPOSITION_CHARGED_OFFENSE_TITLE  Top category: POSSESSION OF A CONTROLLED SUBST...  
DISPOSITION_CHARGED_CHAPTER        Top category: 720 (0.80%) Second category: 625...  
DISPOSITION_CHARGED_ACT            Top category: 5 (0.70%) Second category: 570 (...  
DISPOSITION_CHARGED_SECTION        Top category: 402(c) (0.15%) Second category: ...  
DISPOSITION_CHARGED_CLASS          Top category: 4 (0.41%) Second category: 2 (0....  
DISPOSITION_CHARGED_AOIC           Top category: 5101110 (0.15%) Second category:...  
DISPOSITION_DATE                   Top category: 10/30/2013 12

In [42]:
init_input_df = make_input_df(init)
#init_input_df.to_csv('init_input_df')
init_input_df

Datatype Number of Missing Values  \
CASE_ID                     int64                        0   
CASE_PARTICIPANT_ID         int64                        0   
OFFENSE_CATEGORY           object                        0   
PRIMARY_CHARGE               bool                        0   
CHARGE_ID                   int64                        0   
CHARGE_VERSION_ID           int64                        0   
CHARGE_OFFENSE_TITLE       object                        0   
CHAPTER                    object                        0   
ACT                        object                        8   
SECTION                    object                        8   
CLASS                      object                        0   
AOIC                       object                        0   
EVENT                      object                    21355   
EVENT_DATE                 object                    21355   
AGE_AT_INCIDENT           float64                    17557   
GENDER                     object                     4180   
RACE                       object                     5791   
INCIDENT_BEGIN_DATE        object                    11553   
INCIDENT_END_DATE          object                   806298   
ARREST_DATE                object                    30683   
LAW_ENFORCEMENT_AGENCY     object                     3712   
UNIT                       object                   633918   
INCIDENT_CITY              object                    34905   
RECEIVED_DATE              object                        0   
ARRAIGNMENT_DATE           object                   127086   
UPDATED_OFFENSE_CATEGORY   object                        0   
CHARGE_COUNT                int64                        0   

                                                          Value Information  
CASE_ID                   Top id: 125092548358 (0.00%) Second top id: 11...  
CASE_PARTICIPANT_ID       Top id: 1020802810182 (0.00%) Second top id: 1...  
OFFENSE_CATEGORY          Top category: Narcotics (0.21%) Second categor...  
PRIMARY_CHARGE                                     True: 0.36% False: 0.64%  
CHARGE_ID                 Top id: 2183689993736 (0.00%) Second top id: 2...  
CHARGE_VERSION_ID         Top id: 496384317753 (0.00%) Second top id: 49...  
CHARGE_OFFENSE_TITLE      Top category: AGGRAVATED UNLAWFUL USE OF WEAPO...  
CHAPTER                   Top category: 720 (0.84%) Second category: 625...  
ACT                       Top category: 5 (0.76%) Second category: 570 (...  
SECTION                   Top category: 402(c) (0.10%) Second category: ...  
CLASS                     Top category: 4 (0.40%) Second category: 2 (0....  
AOIC                      Top category: 5101110 (0.10%) Second category:...  
EVENT                     Top category: Preliminary Hearing (0.76%) Seco...  
EVENT_DATE                Top category: 11/12/2019 12:00:00 AM (0.00%) S...  
AGE_AT_INCIDENT                Min: 17.0 Max: 156.0 Mean: 31.99 Median: nan  
GENDER                    Top category: Male (0.89%) Second category: Fe...  
RACE                      Top category: Black (0.67%) Second category: W...  
INCIDENT_BEGIN_DATE       Top category: 2/2/2016 12:00:00 AM (0.00%) Sec...  
INCIDENT_END_DATE         Top category: 8/22/2011 12:00:00 AM (0.01%) Se...  
ARREST_DATE               Top category: 5/18/2016 8:15:00 PM (0.00%) Sec...  
LAW_ENFORCEMENT_AGENCY    Top category: CHICAGO PD (0.67%) Second catego...  
UNIT                      Top category: District 11 - Harrison (0.19%) S...  
INCIDENT_CITY             Top category: Chicago (0.71%) Second category:...  
RECEIVED_DATE             Top category: 5/19/2016 12:00:00 AM (0.00%) Se...  
ARRAIGNMENT_DATE          Top category: 6/28/2016 12:00:00 AM (0.00%) Se...  
UPDATED_OFFENSE_CATEGORY  Top category: Narcotics (0.22%) Second categor...  
CHARGE_COUNT                         Min: 1 Max: 668 Mean: 6.43 Median: 2.0

In [44]:
disp_input_df = make_input_df(dispo)
#disp_input_df.to_csv('disp_input_df')
disp_input_df

Datatype Number of Missing Values  \
CASE_ID                              int64                        0   
CASE_PARTICIPANT_ID                  int64                        0   
OFFENSE_CATEGORY                    object                        0   
PRIMARY_CHARGE                        bool                        0   
CHARGE_ID                            int64                        0   
CHARGE_VERSION_ID                    int64                        0   
DISPOSITION_CHARGED_OFFENSE_TITLE   object                        0   
DISPOSITION_CHARGED_CHAPTER         object                        0   
DISPOSITION_CHARGED_ACT             object                    23341   
DISPOSITION_CHARGED_SECTION         object                    23341   
DISPOSITION_CHARGED_CLASS           object                      170   
DISPOSITION_CHARGED_AOIC            object                      193   
DISPOSITION_DATE                    object                        0   
CHARGE_DISPOSITION                  object                        0   
CHARGE_DISPOSITION_REASON           object                   602411   
JUDGE                               object                    69566   
COURT_NAME                          object                     5550   
COURT_FACILITY                      object                     8469   
AGE_AT_INCIDENT                    float64                    13351   
GENDER                              object                     2945   
RACE                                object                     4183   
INCIDENT_BEGIN_DATE                 object                     7614   
INCIDENT_END_DATE                   object                   729228   
ARREST_DATE                         object                    17929   
LAW_ENFORCEMENT_AGENCY              object                     1062   
UNIT                                object                   571681   
INCIDENT_CITY                       object                    73668   
RECEIVED_DATE                       object                        0   
ARRAIGNMENT_DATE                    object                   141443   
UPDATED_OFFENSE_CATEGORY            object                        0   
CHARGE_COUNT                         int64                        0   

                                                                   Value Information  
CASE_ID                            Top id: 115818625526 (0.00%) Second top id: 12...  
CASE_PARTICIPANT_ID                Top id: 863329937181 (0.00%) Second top id: 90...  
OFFENSE_CATEGORY                   Top category: Narcotics (0.22%) Second categor...  
PRIMARY_CHARGE                                              True: 0.37% False: 0.63%  
CHARGE_ID                          Top id: 2183385951322 (0.00%) Second top id: 2...  
CHARGE_VERSION_ID                  Top id: 496434127094 (0.00%) Second top id: 49...  
DISPOSITION_CHARGED_OFFENSE_TITLE  Top category: POSSESSION OF A CONTROLLED SUBST...  
DISPOSITION_CHARGED_CHAPTER        Top category: 720 (0.82%) Second category: 625...  
DISPOSITION_CHARGED_ACT            Top category: 5 (0.75%) Second category: 570 (...  
DISPOSITION_CHARGED_SECTION        Top category: 402(c) (0.13%) Second category: ...  
DISPOSITION_CHARGED_CLASS          Top category: 4 (0.42%) Second category: 2 (0....  
DISPOSITION_CHARGED_AOIC           Top category: 5101110 (0.13%) Second category:...  
DISPOSITION_DATE                   Top category: 10/30/2013 12:00:00 AM (0.00%) S...  
CHARGE_DISPOSITION                 Top category: Nolle Prosecution (0.61%) Second...  
CHARGE_DISPOSITION_REASON          Top category: PG to Other Count/s (0.58%) Seco...  
JUDGE                              Top category: Brian K Flaherty (0.03%) Second ...  
COURT_NAME                         Top category: District 1 - Chicago (0.61%) Sec...  
COURT_FACILITY                     Top category: 26TH Street (0.54%) Second categ...  
AGE_AT_INCIDENT                         Min: 17.0 Max: 156.0 Mean: 31.91 Median: nan  
GENDER               

## Looking into candidate keys and testing dependencies

In [4]:
init.columns

Index(['CASE_ID', 'CASE_PARTICIPANT_ID', 'OFFENSE_CATEGORY', 'PRIMARY_CHARGE',
       'CHARGE_ID', 'CHARGE_VERSION_ID', 'CHARGE_OFFENSE_TITLE', 'CHAPTER',
       'ACT', 'SECTION', 'CLASS', 'AOIC', 'EVENT', 'EVENT_DATE',
       'AGE_AT_INCIDENT', 'GENDER', 'RACE', 'INCIDENT_BEGIN_DATE',
       'INCIDENT_END_DATE', 'ARREST_DATE', 'LAW_ENFORCEMENT_AGENCY', 'UNIT',
       'INCIDENT_CITY', 'RECEIVED_DATE', 'ARRAIGNMENT_DATE',
       'UPDATED_OFFENSE_CATEGORY', 'CHARGE_COUNT'],
      dtype='object')

In [5]:
dispo.columns

Index(['CASE_ID', 'CASE_PARTICIPANT_ID', 'OFFENSE_CATEGORY', 'PRIMARY_CHARGE',
       'CHARGE_ID', 'CHARGE_VERSION_ID', 'DISPOSITION_CHARGED_OFFENSE_TITLE',
       'DISPOSITION_CHARGED_CHAPTER', 'DISPOSITION_CHARGED_ACT',
       'DISPOSITION_CHARGED_SECTION', 'DISPOSITION_CHARGED_CLASS',
       'DISPOSITION_CHARGED_AOIC', 'DISPOSITION_DATE', 'CHARGE_DISPOSITION',
       'CHARGE_DISPOSITION_REASON', 'JUDGE', 'COURT_NAME', 'COURT_FACILITY',
       'AGE_AT_INCIDENT', 'GENDER', 'RACE', 'INCIDENT_BEGIN_DATE',
       'INCIDENT_END_DATE', 'ARREST_DATE', 'LAW_ENFORCEMENT_AGENCY', 'UNIT',
       'INCIDENT_CITY', 'RECEIVED_DATE', 'ARRAIGNMENT_DATE',
       'UPDATED_OFFENSE_CATEGORY', 'CHARGE_COUNT'],
      dtype='object')

In [6]:
sent.columns

Index(['CASE_ID', 'CASE_PARTICIPANT_ID', 'OFFENSE_CATEGORY', 'PRIMARY_CHARGE',
       'CHARGE_ID', 'CHARGE_VERSION_ID', 'DISPOSITION_CHARGED_OFFENSE_TITLE',
       'DISPOSITION_CHARGED_CHAPTER', 'DISPOSITION_CHARGED_ACT',
       'DISPOSITION_CHARGED_SECTION', 'DISPOSITION_CHARGED_CLASS',
       'DISPOSITION_CHARGED_AOIC', 'DISPOSITION_DATE', 'CHARGE_DISPOSITION',
       'CHARGE_DISPOSITION_REASON', 'SENTENCE_PHASE', 'SENTENCE_DATE',
       'SENTENCE_JUDGE', 'SENTENCE_TYPE', 'CURRENT_SENTENCE',
       'COMMITMENT_TYPE', 'COMMITMENT_TERM', 'COMMITMENT_UNIT', 'COURT_NAME',
       'COURT_FACILITY', 'LENGTH_OF_CASE_in_Days', 'AGE_AT_INCIDENT', 'GENDER',
       'RACE', 'INCIDENT_BEGIN_DATE', 'INCIDENT_END_DATE', 'ARREST_DATE',
       'LAW_ENFORCEMENT_AGENCY', 'UNIT', 'INCIDENT_CITY', 'RECEIVED_DATE',
       'ARRAIGNMENT_DATE', 'UPDATED_OFFENSE_CATEGORY', 'CHARGE_COUNT'],
      dtype='object')

## Indentifying Candidate Keys

In [8]:
def test_dependency(df, col1, col2):
    '''From Brina Seidel's Lab 4 Notebook
    
       Tests whether there is total redundancy betwen col1 and col2
       by testing the number of unique combinations'''
    unique_1 = len(df[col1].unique())
    unique_2 = len(df[col2].unique())
    unique_combos = len(df[[col1, col2]].drop_duplicates())
    print("Unique values of {}: {}".format(col1, unique_1))
    print("Unique values of {}: {}".format(col2, unique_2))
    print("Unique combos of {} and {}: {}".format(col1, col2, unique_combos))
    return unique_combos == max(unique_1, unique_2)

In [9]:
test_dependency(init, 'CASE_PARTICIPANT_ID', 'CHARGE_ID')

Unique values of CASE_PARTICIPANT_ID: 334417
Unique values of CHARGE_ID: 848542
Unique combos of CASE_PARTICIPANT_ID and CHARGE_ID: 904719


False

In [10]:
len(init)

904719

In [11]:
test_dependency(dispo, 'CASE_PARTICIPANT_ID', 'CHARGE_ID')

Unique values of CASE_PARTICIPANT_ID: 312616
Unique values of CHARGE_ID: 779723
Unique combos of CASE_PARTICIPANT_ID and CHARGE_ID: 821723


False

In [12]:
len(dispo)

821723

In [13]:
test_dependency(sent, 'CASE_PARTICIPANT_ID', 'CHARGE_ID')

Unique values of CASE_PARTICIPANT_ID: 201181
Unique values of CHARGE_ID: 217597
Unique combos of CASE_PARTICIPANT_ID and CHARGE_ID: 227049


False

In [14]:
len(sent)

236124

#### We see that 'CASE_PARTICIPANT_ID' + 'CHARGE_ID' forms a candidate key in the Initiation and Dispositions datasets, but not in Sentencing. This indicates that each row in Initiation and Disposition represents a single charge against a person.

## Looking for Candidate Key in Sentencing Dataset

In [15]:
# Algorithm inspired by A Priori / Candidate Generation

'''
Use CP ID, Charge ID, Charge Version ID, and sentencing-related features
as potential building blocks for candidate key
'''

F = {1:[['CASE_PARTICIPANT_ID'], ['CHARGE_ID'], ['CHARGE_VERSION_ID'],
        ['SENTENCE_PHASE'], ['SENTENCE_DATE'], ['SENTENCE_JUDGE'], 
        ['SENTENCE_TYPE'], ['CURRENT_SENTENCE'],['COMMITMENT_TYPE'], 
        ['COMMITMENT_TERM'], ['COMMITMENT_UNIT'], ['COURT_NAME'],
        ['COURT_FACILITY'], ['LENGTH_OF_CASE_in_Days']]}

candidate_keys=[]

In [16]:
for k in range(1,len(F[1])):
    print('k='+str(k))
    F[k+1]=[]
    for group in F[k]:
        print('\t group: ', group)
        for col in F[1]:
            if col[0] not in group and group[-1]<col[0]:
                new_group = group.copy()+col
                if len(sent[new_group].drop_duplicates())==len(sent):
                    print('Candidate key: ', new_group)
                    candidate_keys.append(new_group)
                else:
                #search for further supersets if candidate key not identified
                    F[k+1].append(new_group)
                    print('\t\t new_group: ', new_group)

k=1
	 group:  ['CASE_PARTICIPANT_ID']
		 new_group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID']
		 new_group:  ['CASE_PARTICIPANT_ID', 'CHARGE_VERSION_ID']
		 new_group:  ['CASE_PARTICIPANT_ID', 'SENTENCE_PHASE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'SENTENCE_DATE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'SENTENCE_JUDGE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'SENTENCE_TYPE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'CURRENT_SENTENCE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_UNIT']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COURT_NAME']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COURT_FACILITY']
		 new_group:  ['CASE_PARTICIPANT_ID', 'LENGTH_OF_CASE_in_Days']
	 group:  ['CHARGE_ID']
		 new_group:  ['CHARGE_ID', 'CHARGE_VERSION_ID']
		 new_group:  ['CHARGE_ID', 'SENTENCE_PHASE']
		 new_group:  ['CHARGE_ID', 'SENTENCE_DATE']
		 new_group:  ['CHARGE_ID', 'SENTENCE_JUDGE']
		

		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'SENTENCE_DATE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'SENTENCE_JUDGE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'SENTENCE_TYPE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'CURRENT_SENTENCE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'COURT_NAME']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'COURT_FACILITY']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'LENGTH_OF_CASE_in_Days']
	 group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM', 'SENTENCE_PHASE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM', 'SENTENCE_DATE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM', 'SENTENCE_JUDGE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM', 'SENTENCE_TYPE']
		 new_group:  ['CASE_PARTICIPAN

		 new_group:  ['CHARGE_ID', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_TYPE']
	 group:  ['CHARGE_VERSION_ID', 'SENTENCE_PHASE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_VERSION_ID', 'SENTENCE_DATE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_DATE', 'SENTENCE_PHASE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_DATE', 'SENTENCE_JUDGE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_DATE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_VERSION_ID', 'SENTENCE_JUDGE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_JUDGE', 'SENTENCE_PHASE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_VERSION_ID', 'SENTENCE_TYPE']
	 group:  ['CHARGE_VERSION_ID', 'CURRENT_SENTENCE']
		 new_group:  ['CHARGE_VERSION_ID', 'CURRENT_SENTENCE', 'SENTENCE_PHASE']
		 new_group:  ['CHARGE_VERSION_ID', 'CURRENT_SENTENCE', 'SENTENCE_DATE']
		 new_group:  ['CHARGE_VERSION_ID', 'CURRENT_SENTENCE', 'SENTENCE_JUDGE']
		 new_group:  ['CHARG

		 new_group:  ['COMMITMENT_TYPE', 'COURT_NAME', 'CURRENT_SENTENCE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days']
	 group:  ['COMMITMENT_TYPE', 'COURT_FACILITY']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'SENTENCE_PHASE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'SENTENCE_DATE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'SENTENCE_JUDGE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'SENTENCE_TYPE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'CURRENT_SENTENCE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'LENGTH_OF_CASE_in_Days']
	 group:  ['COMMITMENT_TYPE', 'LENGTH_OF_CASE_in_Days']
		 new_group:  ['COMMITMENT_TYPE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_PHASE']
		 new_group:  ['COMMITMENT_TYPE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE']
		 new_group:  ['COMMITMENT_TYPE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE']
		 new_group:  

		 new_group:  ['COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE']
		 new_group:  ['COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE']
		 new_group:  ['COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_TYPE']
	 group:  ['COURT_FACILITY', 'SENTENCE_PHASE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['COURT_FACILITY', 'SENTENCE_DATE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_DATE', 'SENTENCE_PHASE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_DATE', 'SENTENCE_JUDGE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_DATE', 'SENTENCE_TYPE']
	 group:  ['COURT_FACILITY', 'SENTENCE_JUDGE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_JUDGE', 'SENTENCE_PHASE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['COURT_FACILITY', 'SENTENCE_TYPE']
	 group:  ['COURT_FACILITY', 'CURRENT_SENTENCE']
		 new_group:  ['COURT_FACILITY', 'CURRENT_SENTENCE', 'SENTENCE_PHASE']
		 new_group:  ['COURT_FACILITY', 'CURRENT_SENTENCE', 'SENT

...

		 new_group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF

		 new_group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_UNIT', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_O

		 new_group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 

Candidate key:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID',

		 new_group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMM

In [17]:
# view all candidate keys
candidate_keys

[['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_VERSION_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'CHARGE_VERSION_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_JUDGE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'LENGTH_OF_CASE_in_Days',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'COMMITMENT_UNIT',
  '

In [18]:
# candidate keys of minimum length
[x for x in candidate_keys if len(x)==8]

[['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_VERSION_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE']]

In [19]:
# check for candidate keys that do not contain 'COMMITMENT_TERM'
[x for x in candidate_keys if 'COMMITMENT_TERM' not in x]

[]

#### Business rules that govern row-generation in the Sentencing dataset still not clear.

## Investigating Relationship between CHARGE_ID and CHARGE_VERSION_ID

In [20]:
test_dependency(dispo, 'CHARGE_ID', 'CHARGE_VERSION_ID')

Unique values of CHARGE_ID: 779723
Unique values of CHARGE_VERSION_ID: 784137
Unique combos of CHARGE_ID and CHARGE_VERSION_ID: 784137


True

In [21]:
test_dependency(init, 'CHARGE_ID', 'CHARGE_VERSION_ID')

Unique values of CHARGE_ID: 848542
Unique values of CHARGE_VERSION_ID: 848542
Unique combos of CHARGE_ID and CHARGE_VERSION_ID: 848542


True

In [22]:
test_dependency(sent, 'CHARGE_ID', 'CHARGE_VERSION_ID')

Unique values of CHARGE_ID: 217597
Unique values of CHARGE_VERSION_ID: 220786
Unique combos of CHARGE_ID and CHARGE_VERSION_ID: 220786


True

#### This shows that in all three datasets, each CHARGE_VERSION_ID corresponds to exactly 1 CHARGE_ID.

## Investigating Relationship between CASE_PARTICIPANT_ID and CASE_ID

In [23]:
test_dependency(init, 'CASE_PARTICIPANT_ID', 'CASE_ID')

Unique values of CASE_PARTICIPANT_ID: 334417
Unique values of CASE_ID: 310135
Unique combos of CASE_PARTICIPANT_ID and CASE_ID: 334417


True

In [24]:
test_dependency(dispo, 'CASE_PARTICIPANT_ID', 'CASE_ID')

Unique values of CASE_PARTICIPANT_ID: 312616
Unique values of CASE_ID: 291211
Unique combos of CASE_PARTICIPANT_ID and CASE_ID: 312616


True

In [25]:
test_dependency(sent, 'CASE_PARTICIPANT_ID', 'CASE_ID')

Unique values of CASE_PARTICIPANT_ID: 201181
Unique values of CASE_ID: 187239
Unique combos of CASE_PARTICIPANT_ID and CASE_ID: 201181


True

#### This confirms that in all 3 datasets, each CP ID corresponds to 1 person and 1 case.